## Exercise 13: The Variational Quantum Eigensolver (VQE)

In this exercise we are going to see how variational methods can be used in a hybrid quantum-classical scheme in order to approximate quantum states.

In particular the aim of the Variational Quantum Eigensolver (VQE) is to optimize a set of parameterized quantum gates to approximate the ground state of a quantum system, given that the expectation value of the energy and its derivatives with respect to the parameters are evaluated on a quantum hardware in a scalable way.

Preparing ground state is an exponentially complex task even on a quantum computer (QMA), but the VQE is expected to give some advantage for specific tasks in physics, chemistry and/or material sciences.

### Classical simulation of $H_2$ 

Here we will recall the code for the classical simulation of the dissociation process of $H_2$ diatomic molecule.

In [1]:
#!pip install pyscf

In [2]:
import numpy as np
from pyscf import gto,scf,ao2mo,mp,cc,fci,tools
import matplotlib.pyplot as plt

np.set_printoptions(precision=2,suppress=1e-8,linewidth=120)

In [ ]:
## Define a set of distances between the two atoms

distances = np.arange(0.3, 4, .05)

## and a basis in which the calculations will be made

basis = 'sto-6g' #'6-31g' 'cc-pvdz' 'aug-cc-pvdz' ,...

## Define a dictionary containing the energies derived with different methods
energies = {}

In [ ]:
energies["HF_"+basis]   = []
energies["FCI_"+basis]  = []
energies["CCSD_"+basis] = []

for (i,r) in enumerate(distances):
    # Build the 3D geometry of the molecule
    geometry = "H .0 .0 .0; H .0 .0 "+str(r)
    # And pass it to the gaussian orbitals generator (this is an alternative way to create the molecule object)
    mol = gto.M(atom=geometry,charge=0,spin=0,basis=basis,symmetry=True,verbose=0)
    
    mf  = scf.RHF(mol) # Initialise a Restricted HF calculation using the molecule constructed
    Ehf = mf.kernel()  #<- calling the kernel we compute the energy using the orbitals obtained
    
    fci_h2 = fci.FCI(mf) # FCI calculation
    Efci = fci_h2.kernel()[0]
    
    
    ccsd_h2 = cc.CCSD(mf) # CCSD calculation
    e_ccsd  = ccsd_h2.kernel()[0]
    e_ccsd += Ehf # <- this lines is mandatory because CCSD computes the energy difference with HF
    
    
    # Save energies
    energies["HF_"+basis].append(Ehf)
    energies["FCI_"+basis].append(Efci)
    energies["CCSD_"+basis].append(e_ccsd)

In [ ]:
## Now plot the result

plt.plot(distances,energies["HF_"+basis],label="HF - "+basis)
plt.plot(distances,energies["FCI_"+basis],label="FCI - "+basis)
plt.plot(distances,energies["CCSD_"+basis],label="CCSD - "+basis,linestyle="",marker=".")

plt.xlabel(r"$r$ [$\AA$]")
plt.ylabel(r"$E$ [Hartree]")
plt.legend()
plt.show()

As can be seen, the CCSD calculation is as accurate as FCI in this small system.

### Quantum simulation of $H_2$

Now we will proceed to the simulation on the quantum computer.

As showed [here](https://www.nature.com/articles/nature23879) the Variational quantum eigensolver can be used to calculate dissociation processes of small molecules on quantum processor.

In [ ]:
from qiskit import QuantumCircuit
from qiskit_aer import Aer
from qiskit.circuit import ParameterVector
from qiskit.quantum_info import SparsePauliOp # To create operators
from qiskit.primitives import Estimator       # to estimate expectation values

#### Preparing the Hamiltonian

First, since we want to study a fermionic system on a set of qubits, we must find a mapping between the two.

The oldest mapping proposed is the Jordan-Wigner, which was illustrated also in the lectures, but there are many others.

Two noticeable alternatives are the [parity mapping](https://iopscience.iop.org/article/10.1088/1367-2630/aac54f) and the [Bravyi-Kitaev mapping](https://pubs.acs.org/doi/10.1021/acs.jctc.8b00450).

In particular, we are going to focus on the parity mapping for the $H_2$ system. 

Instead of storing the occupation of a fermionic state $f_{j}$, as Jordan-Wigner does, this isomorphism uses the qubits to store the quantity 
\begin{equation}
\label{eq:parity}
p_{j}=\sum_{i=0}^{j-1}f_{i} \mod 2 \quad ,
\end{equation}
called parity of the set of occupation numbers $f_{j-1}\dots f_{0}$. 

This is convenient for system like $H_2$ which conserve the total number of electrons with fixed spin orientation, meaning that we can get rid of two qubits out of the box.

Manually performing the mapping can be a very tedious and prone-to-error task, for this reason we will use the very practical Qiskit PySCF driver, which recalls the creation of a PySCF molecule object that we have seen in previous lectures but gives a qubit operator ready to be measured on a quantum computer.

This driver can be found in the Qiskit optional package `nature`.

In [ ]:
#!pip install 'qiskit-nature'

In [ ]:
from qiskit_nature.second_q.drivers import PySCFDriver
from qiskit_nature.second_q.formats.molecule_info import MoleculeInfo

In [ ]:
# Initialise the molecule using the PySCF driver

molecule = MoleculeInfo(["H", "H"], [(0.0, 0.0, 0.0), (0.0, 0.0, 0.735)], charge=0, multiplicity=1)
driver = PySCFDriver.from_molecule(molecule, basis="sto6g")
problem = driver.run()

In [ ]:
# Now the problem has also the nuclear repulsion shift of the Born-Oppenheimer approximation
problem.nuclear_repulsion_energy

In [ ]:
## Calling .second_q_ops will generate a bunch of operators such as dipole, magnetization, ...
## We only need the Hamiltonian
hamiltonian = problem.second_q_ops()[0]

In [ ]:
print(hamiltonian)

In [ ]:
## Now we will map the problem to a qubit operator
from qiskit_nature.second_q.mappers import JordanWignerMapper, BravyiKitaevMapper, ParityMapper

In [ ]:
## Create the qubit operator 
#mapper = JordanWignerMapper()
#mapper = BravyiKitaevMapper()
mapper = ParityMapper()
qubit_op = mapper.map(hamiltonian)
print(qubit_op)

In [ ]:
## Create the qubit operator (With 2 qubit reduction)
mapper = ParityMapper(num_particles=problem.num_particles) # Parity mapper requires the spin up and down electrons
qubit_op = mapper.map(hamiltonian)
print(qubit_op)

Now we have seen how to create a qubit operator for a single configuration, we will need to repeat this procedure for every $r$ in order to study the dissociation process of $H_2$.

#### Initial state

We need a starting point for our calculations, that in this case will be the Hartree-Fock (HF) determinant.
This can be easily prepared on the quantum circuit, since we are already in the basis of the HF orbitals.
This means that we will need to put an $X$ gate if the corresponding spin-orbital is occupied (Jordan-Wigner) or it has a odd occupation number (Parity). 

Qiskit provides a useful `HartreeFock` function to create this initial state, that then we will pass to the VQE function.

In [ ]:
from qiskit_nature.second_q.circuit.library.initial_states import HartreeFock

In [ ]:
init_state = HartreeFock(num_spatial_orbitals=problem.num_spatial_orbitals, num_particles=problem.num_particles, qubit_mapper=mapper)
init_state.draw("mpl")

#### Variational wave function

Now that we have the Hamiltonian operator, we will need an ansatz for our wavefunction. Since we need a variational ansatz, some gates will contains parameters that are going to be iteratively optimized (as an example, rotation on the $x,y,z$ axis).

There is no analytical way to choose an ansatz for the system: there are empirical rules based on similarity with what we are studying.
Some ans&auml;tze come from classical computational chemistry, such as the highly accurate [q-UCCSD](https://arxiv.org/pdf/1506.00443.pdf),  but mostly we have to consider some circuits that can be run on current devices, so they have to contain few two qubits gates and be relatively shallow: these ans&auml;tze are called hardware-efficient.


What we are going to consider is one of the so-called "hardware-efficient ans&auml;tze". 
The system does not contain many qubits, so our trial ansatz will be very simple : a layer of rotations around the $y$-axis followed by CNOTs and again a layer of rotations. This simple structure can be easily extended both in depth (adding more CNOTs and rotation) and in width, to study bigger system, therefore is widely used.

In [ ]:
def variational_ansatz(n_qubits,params):
    
    qc = QuantumCircuit(n_qubits)
    
    for i in range(n_qubits):
        qc.ry(params[i],i)
    qc.barrier()
    for i in range(n_qubits-1):
        qc.cx(i,i+1)
    qc.barrier()
    for i in range(n_qubits):
        qc.ry(params[n_qubits+i],i)
    return qc

In [ ]:
## Let's plot an example

params = ParameterVector('θ',10)
variational_ansatz(5, params).draw("mpl")

#### Evaluating energy and the gradient

Now we focus on the core part of the VQE algorithm: the evaluation of the energy and of its gradient on the quantum hardware.

Qiskit has built-in methods for this, but we are going to implement ours from scratch.

First, we want a circuit to measure the expecation value of the Hamiltonian on our trial state

In [ ]:
def energy(quantum_circuit, hamiltonian, parameters, estimator):
    ## This function evaluates the energy during a VQE calculation
    return estimator.run(quantum_circuit, hamiltonian, parameters).result().values[0]

In [ ]:
## Example energy estimation
param_vec = ParameterVector("θ",4)
q_circuit = variational_ansatz(2,param_vec)
estimator = Estimator()

In [ ]:
energy(q_circuit, qubit_op, np.random.rand(4), estimator)

Now things get interesting! In order to optimize our parameters $\theta$, a quantum computer has to give to classical optimizer important information such as first- or second-order derivatives! But how can we measure the derivative wrt to a specific parameter on a quantum circuit?

$$
\frac{\partial }{\partial \theta_i} L(\theta) = \frac{\partial }{\partial \theta_i} \langle \psi(\theta) | H | \psi(\theta) \rangle
$$

many different methods have been proposed recently, in this case we are going to see a method  that is called _parameter shift_:

- assume that every parametrized gate is of the form $$ U_j(\theta_j) = e^{-i \theta_j G_j}= \cos(\theta_j)\mathbf{I} -i \sin(\theta_j)G_j$$ where $G_j$ is an operator such that $G_{j}^{2} = \mathbf{I}$

- then the derivative can be expressed as $$ \frac{\partial }{\partial \theta_i} L(\theta) = \frac{L(\theta+ e_i s)-L(\theta-e_is)}{2\sin(s)}  $$ where $s \in \mathbf{R}$ and $e_i$ indicates the versor in the $i$-th direction. In our case we are going to consider $s= \frac{\pi}{2}$.

This means that to calculate the gradient with $N_p$ parameters, we have to measure $H$ on $2N_p$ different circuits, but it's possible!

Note that the assumption we made is quite general: $G_j$ could be every tensor product of Pauli operators

In [ ]:
#useful function to shift the parameters
def ei(i,n):
    '''unit vector in direction i of size n'''
    vi = np.zeros(n)
    vi[i] = 1.0
    return vi[:]


def gradient(quantum_circuit, hamiltonian, parameters, estimator):

    # TODO implement the gradient with the parameter-shift rule
    # you need to pass the estimator object to the energy(...) function defined above.

    # g = ...
    # return g
    pass

#### The VQE algorithm

Now we declare a function to repeat iteratively the procedure of measuring energy, its gradient and then optimizing the parameters using a standard gradient descent technique, namely $$ \theta_{new}= \theta_{old} - \eta \nabla_{\theta} L(\theta)$$ with $\eta \in \mathbf{R}$ as the learning rate.

In [ ]:
def VQE(operator=None, ansatz=None, init_params=None, init_state=None, estimator=None, max_iter=100, lr=0.1):
    """
    Args: 
        operator: the hamiltonian as a qubit operator
        ansatz: the variational ansatz
        init_params: the initital parameters
        init_state: circuit to prepare the initial state (e.g. the Hartree-Fock state)
        estimator: qiskit Estimator object, to be passed to energy(...) and gradient(...)
        max_iter: number of gradient descent iterations
        lr: learning rate η
    Returns:
        energies: list of estimated energies at each step of the vqe 
        gradients:  list of estimated gradients at each step of the vqe 
    """
    # compose initial state preparation and ansatz
    quantum_circuit = init_state.compose(ansatz(operator.num_qubits, ParameterVector('θ', len(init_params))))
    
    # TODO implement the vqe using the energy(...) and gradient(...) functions defined above
    
    # energies = ...
    # gradients = ...
    # return energies, gradients

#### Perform the optimization on a single configuration

In [ ]:
molecule    = MoleculeInfo(["H", "H"], [(0.0, 0.0, 0.0), (0.0, 0.0, 0.735)], charge=0, multiplicity=1)
driver      = PySCFDriver.from_molecule(molecule, basis="sto6g")
problem     = driver.run()
hamiltonian = problem.second_q_ops()[0]
    
nucl_shift  = problem.nuclear_repulsion_energy


mapper      = ParityMapper(num_particles=problem.num_particles) # Parity mapper requires the spin up and down electrons
qubit_op    = mapper.map(hamiltonian)

In [ ]:
# Now create the circuit
n_qubits    = qubit_op.num_qubits
init_params = np.random.rand(2*n_qubits)
init_state  = HartreeFock(num_spatial_orbitals=problem.num_spatial_orbitals, num_particles=problem.num_particles, qubit_mapper=mapper)


n_reps = 50
lr = 0.5
estimator = Estimator()

energies_vqe, gradients_vqe = VQE(qubit_op,variational_ansatz,init_params,init_state,estimator,n_reps,lr)

In [ ]:
steps = list(range(n_reps))

plt.figure(figsize=(4.8,3.4),dpi=100)
plt.errorbar(steps,np.array(energies_vqe)+nucl_shift,marker='o',linestyle='dashed',label="VQE")
plt.hlines(-1.145, xmin= -10, xmax= 1000,label='Theoretical',linestyle ='dashed',color='black')
plt.xlabel('Step')
plt.xlim(xmin=-1,xmax=51)
plt.ylabel('Energy')

plt.show()

#### Quantum simulation

Now we are going to perform the VQE algorithm for every configuration of the $H_2$ molecule.

In [ ]:
# Prepare the backend
estimator = Estimator()
vqe_distances = list(np.arange(0.3, 1.5, .1)) + list(np.arange(1.5, 4.0, .2))

energies["VQE_"+basis] = []
energies["VQE_error"+basis] = []

# Repeat for every r
for (i,r) in enumerate(vqe_distances):
    print("\n=======================================")
    print(f" DISTANCE: {r:0.3}")
    print("=======================================\n")
    
    molecule    = MoleculeInfo(["H", "H"], [(0.0, 0.0, 0.0), (0.0, 0.0, r)], charge=0, multiplicity=1)
    driver      = PySCFDriver.from_molecule(molecule, basis="sto6g")
    problem     = driver.run()
    nucl_shift  = problem.nuclear_repulsion_energy
    
    
    # Build the (reduced) qubit operator
    hamiltonian = problem.second_q_ops()[0]
    mapper     = ParityMapper(num_particles=problem.num_particles)
    qubit_op   = mapper.map(hamiltonian)
    
    # Now create the circuit
    n_qubits   = qubit_op.num_qubits
    params     = np.random.rand(2*n_qubits)
    init_state = HartreeFock(num_spatial_orbitals=problem.num_spatial_orbitals, num_particles=problem.num_particles, qubit_mapper=mapper)
    
    #Run the algorithm
    n_reps  = 150
    lr = 0.5
    energies_vqe, gradients_vqe = VQE(qubit_op,variational_ansatz,params,init_state,estimator,n_reps,lr)
    
    print("Final energy: ",energies_vqe[-1]+nucl_shift)
    
    energies["VQE_"+basis].append(energies_vqe[-1]+nucl_shift)

#### Plot the final results

In [ ]:
plt.plot(distances,energies["HF_"+basis],linestyle="dashed",label="HF - "+basis)
plt.plot(distances,energies["FCI_"+basis],label="FCI - "+basis)
plt.errorbar(vqe_distances,energies["VQE_"+basis],label="VQE - "+basis,linestyle="",marker="o",markersize=5,mew=0.5,mec="black")

plt.xlabel(r"$r$ [$\AA$]")
plt.ylabel(r"$E$ [Hartree]")
plt.legend()
plt.show()